from google.colab import drive

drive.mount('/content/drive')

!unzip /content/drive/MyDrive/data.zip

In [1]:
train_raincityscapes_path = "/home/gregory/Documents/RainPerception/RainRemoval/Copied"

test_raincityscapes_path = "/home/gregory/Documents/RainPerception/RainRemoval/Copied"

In [2]:
import datetime
import os
import torch
import os.path
from torch import nn
from torch import optim
from torch.autograd import Variable
from torch.backends import cudnn
from torch.utils.data import DataLoader
from torchvision import transforms
import random
from PIL import Image
import torch.nn.functional as F
import torch.utils.data as data
import numpy as np

In [3]:
class Compose(object):
    def __init__(self, transforms):
        self.transforms = transforms

    def __call__(self, img, mask, depth):
        assert img.size == mask.size
        assert img.size == depth.size
        for t in self.transforms:
            img, mask, depth = t(img, mask, depth)
        return img, mask, depth

class Resize(object):
    def __init__(self, size):
        self.size = tuple(reversed(size))  # size: (h, w)

    def __call__(self, img, mask, depth):
        assert img.size == mask.size
        assert img.size == depth.size
        return img.resize(self.size, Image.BILINEAR), mask.resize(self.size, Image.BILINEAR), depth.resize(self.size, Image.BILINEAR)


class RandomCrop(object):
    def __init__(self, size):
        self.size = size

    def __call__(self, img, mask, depth):
        assert img.size == mask.size
        assert img.size == depth.size
        w, h = img.size

        x1 = random.randint(0, w - self.size)
        y1 = random.randint(0, h - self.size)
        return img.crop((x1, y1, x1 + self.size, y1 + self.size)), mask.crop((x1, y1, x1 + self.size, y1 + self.size)), depth.crop((x1, y1, x1 + self.size, y1 + self.size))


class RandomHorizontallyFlip(object):
    def __call__(self, img, mask, depth):
        if random.random() < 0.5:
            return img.transpose(Image.FLIP_LEFT_RIGHT), mask.transpose(Image.FLIP_LEFT_RIGHT), depth.transpose(Image.FLIP_LEFT_RIGHT)
        return img, mask, depth

In [4]:
class AvgMeter(object):
    def __init__(self):
        self.reset()

    def reset(self):
        self.val = 0
        self.avg = 0
        self.sum = 0
        self.count = 0

    def update(self, val, n=1):
        self.val = val
        self.sum += val * n
        self.count += n
        self.avg = self.sum / self.count


def check_mkdir(dir_name):
    if not os.path.exists(dir_name):
        os.mkdir(dir_name)


class ReplayBuffer():
    def __init__(self, max_size=50):
        assert (max_size > 0), 'Empty buffer or trying to create a black hole. Be careful.'
        self.max_size = max_size
        self.data = []

    def push_and_pop(self, data):
        to_return = []
        for element in data.data:
            element = torch.unsqueeze(element, 0)
            if len(self.data) < self.max_size:
                self.data.append(element)
                to_return.append(element)
            else:
                if random.uniform(0,1) > 0.5:
                    i = random.randint(0, self.max_size-1)
                    to_return.append(self.data[i].clone())
                    self.data[i] = element
                else:
                    to_return.append(element)
        return Variable(torch.cat(to_return))


def mse_loss(input, target):
    return torch.sum((input - target)**2) / input.data.nelement()


def weights_init_normal(m):
    classname = m.__class__.__name__
    if classname.find('Conv') != -1:
        torch.nn.init.normal_(m.weight.data, 0.0, 0.02)
    elif classname.find('BatchNorm2d') != -1:
        torch.nn.init.normal_(m.weight.data, 1.0, 0.02)
        torch.nn.init.constant_(m.bias.data, 0.0)

In [5]:
def make_dataset(root, is_train):
    if is_train:

        input = open(os.path.join(root, 'data/train_images.txt'))
        ground_t = open(os.path.join(root, 'data/train_gt.txt'))
        depth_t = open(os.path.join(root, 'data/train_depth.txt'))
        image = [(os.path.join(root, 'data/images', img_name.strip('\n'))) for img_name in
                 input]
        gt = [(os.path.join(root, 'data/gt', img_name.strip('\n'))) for img_name in
                 ground_t]
        depth = [(os.path.join(root, 'data/depth', img_name.strip('\n'))) for img_name in
              depth_t]

        input.close()
        ground_t.close()
        depth_t.close()

        return [[image[i], gt[i], depth[i]]for i in range(len(image))]

    else:

        input = open(os.path.join(root, 'data/test_images.txt'))
        ground_t = open(os.path.join(root, 'data/test_gt.txt'))
        depth_t = open(os.path.join(root, 'data/test_depth.txt'))

        image = [(os.path.join(root, 'data/images', img_name.strip('\n'))) for img_name in
                 input]
        gt = [(os.path.join(root, 'data/gt', img_name.strip('\n'))) for img_name in
              ground_t]
        depth = [(os.path.join(root, 'data/depth', img_name.strip('\n'))) for img_name in
                 depth_t]

        input.close()
        ground_t.close()
        depth_t.close()
        
  
        return [[image[i], gt[i], depth[i]]for i in range(len(image))]



class ImageFolder(data.Dataset):
    def __init__(self, root, triple_transform=None, transform=None, target_transform=None, is_train=True):
        self.root = root
        self.imgs = make_dataset(root, is_train)
        self.triple_transform = triple_transform
        self.transform = transform
        self.target_transform = target_transform

    def __getitem__(self, index):
        img_path, gt_path, depth_path = self.imgs[index]
        
        img = Image.open(img_path)
        target = Image.open(gt_path)
        depth = Image.open(depth_path)

        if len(img.getbands()) == 4:
          temp = np.asarray(img)
          temp = temp[:,:,:3]
          img = Image.fromarray(temp)
        if len(target.getbands()) == 4:
          temp = np.asarray(target)
          temp = temp[:,:,:3]
          target = Image.fromarray(temp)
          
        if self.triple_transform is not None:
            img, target, depth = self.triple_transform(img, target, depth)
        if self.transform is not None:
            img = self.transform(img)
        if self.target_transform is not None:
            target = self.target_transform(target)
            depth = self.target_transform(depth)
          
        return img, target, depth

    def __len__(self):
        return len(self.imgs)

In [6]:
cudnn.benchmark = True

ckpt_path = '/home/gregory/Documents/RainPerception/RainRemoval/Copied/ckpt'
exp_name = 'DGNLNet'

args = {
    'iter_num': 40000,
    'train_batch_size': 4,
    'last_iter': 0,
    'lr': 5e-4,
    'lr_decay': 0.9,
    'weight_decay': 0,
    'momentum': 0.9,
    'resume_snapshot': '',
    'val_freq': 500,
    'img_size_h': 512,
	'img_size_w': 1024,
	'crop_size': 512,
    'snapshot_epochs': 1000
}

In [7]:
transform = transforms.Compose([
    transforms.ToTensor()
    #transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
])
to_pil = transforms.ToPILImage()
triple_transform = Compose([
    Resize((args['img_size_h'], args['img_size_w'])),
    #triple_transforms.RandomCrop(args['crop_size']),
    RandomHorizontallyFlip()
])

In [8]:
train_set = ImageFolder(train_raincityscapes_path, transform=transform, target_transform=transform, is_train = True,triple_transform=triple_transform)
train_loader = DataLoader(train_set, batch_size=args['train_batch_size'], num_workers=4, shuffle=True)
test1_set = ImageFolder(test_raincityscapes_path, transform=transform, target_transform=transform, is_train=False)
test1_loader = DataLoader(test1_set, batch_size=2)

In [9]:
len(train_set)

12595

In [10]:
criterion = nn.L1Loss()
criterion_depth = nn.L1Loss()
log_path = os.path.join(ckpt_path, exp_name, str(datetime.datetime.now()) + '.txt')

In [11]:
class DGNL(nn.Module):
    def __init__(self, in_channels):
        super(DGNL, self).__init__()

        self.eps = 1e-6
        self.sigma_pow2 = 100

        self.theta = nn.Conv2d(in_channels, int(in_channels / 2), kernel_size=1)
        self.phi = nn.Conv2d(in_channels, int(in_channels / 2), kernel_size=1)
        self.g = nn.Conv2d(in_channels, int(in_channels / 2), kernel_size=1)

        self.down = nn.Conv2d(in_channels, in_channels, kernel_size=4, stride=4, groups=in_channels, bias=False)
        self.down.weight.data.fill_(1. / 16)

        self.z = nn.Conv2d(int(in_channels / 2), in_channels, kernel_size=1)



    def forward(self, x, depth_map):
        n, c, h, w = x.size()
        x_down = self.down(x)

		# [n, (h / 8) * (w / 8), c / 2]
        g = F.max_pool2d(self.g(x_down), kernel_size=2, stride=2).view(n, int(c / 2), -1).transpose(1, 2)

        ### appearance relation map
        # [n, (h / 4) * (w / 4), c / 2]
        theta = self.theta(x_down).view(n, int(c / 2), -1).transpose(1, 2)
        # [n, c / 2, (h / 8) * (w / 8)]
        phi = F.max_pool2d(self.phi(x_down), kernel_size=2, stride=2).view(n, int(c / 2), -1)

		# [n, (h / 4) * (w / 4), (h / 8) * (w / 8)]
        Ra = F.softmax(torch.bmm(theta, phi), 2)


        ### depth relation map
        depth1 = F.interpolate(depth_map, size=[int(h / 4), int(w / 4)], mode='bilinear', align_corners = True).view(n, 1, int(h / 4)*int(w / 4)).transpose(1,2)
        depth2 = F.interpolate(depth_map, size=[int(h / 8), int(w / 8)], mode='bilinear', align_corners = True).view(n, 1, int(h / 8)*int(w / 8))

        # n, (h / 4) * (w / 4), (h / 8) * (w / 8)
        depth1_expand = depth1.expand(n, int(h / 4) * int(w / 4), int(h / 8) * int(w / 8))
        depth2_expand = depth2.expand(n, int(h / 4) * int(w / 4), int(h / 8) * int(w / 8))

        Rd = torch.min(depth1_expand / (depth2_expand + self.eps), depth2_expand / (depth1_expand + self.eps))

        Rd = F.softmax(Rd, 2)

        S = F.softmax(Ra * Rd, 2)


        # [n, c / 2, h / 4, w / 4]
        y = torch.bmm(S, g).transpose(1, 2).contiguous().view(n, int(c / 2), int(h / 4), int(w / 4))

        return x + F.upsample(self.z(y), size=x.size()[2:], mode='bilinear', align_corners = True)



class NLB(nn.Module):
    def __init__(self, in_channels):
        super(NLB, self).__init__()
        self.theta = nn.Conv2d(in_channels, int(in_channels / 2), kernel_size=1)
        self.phi = nn.Conv2d(in_channels, int(in_channels / 2), kernel_size=1)
        self.g = nn.Conv2d(in_channels, int(in_channels / 2), kernel_size=1)

        self.down = nn.Conv2d(in_channels, in_channels, kernel_size=4, stride=4, groups=in_channels, bias=False)
        self.down.weight.data.fill_(1. / 16)

        self.z = nn.Conv2d(int(in_channels / 2), in_channels, kernel_size=1)

    def forward(self, x):
        n, c, h, w = x.size()
        x_down = self.down(x)

        # [n, (h / 4) * (w / 4), c / 2]
        theta = self.theta(x_down).view(n, int(c / 2), -1).transpose(1, 2)
        # [n, c / 2, (h / 8) * (w / 8)]
        phi = F.max_pool2d(self.phi(x_down), kernel_size=2, stride=2).view(n, int(c / 2), -1)
        # [n, (h / 8) * (w / 8), c / 2]
        g = F.max_pool2d(self.g(x_down), kernel_size=2, stride=2).view(n, int(c / 2), -1).transpose(1, 2)
        # [n, (h / 4) * (w / 4), (h / 8) * (w / 8)]
        f = F.softmax(torch.bmm(theta, phi), 2)
        # [n, c / 2, h / 4, w / 4]
        y = torch.bmm(f, g).transpose(1, 2).contiguous().view(n, int(c / 2), int(h / 4), int(w / 4))

        return x + F.upsample(self.z(y), size=x.size()[2:], mode='bilinear', align_corners=True)


class DepthWiseDilatedResidualBlock(nn.Module):
    def __init__(self, reduced_channels, channels, dilation):
        super(DepthWiseDilatedResidualBlock, self).__init__()
        self.conv0 = nn.Sequential(

		    # pw
		    nn.Conv2d(channels, channels * 2, 1, 1, 0, 1, bias=False),
			nn.ReLU6(inplace=True),
		    # dw
		    nn.Conv2d(channels*2, channels*2, kernel_size=3, padding=dilation, dilation=dilation, groups=channels, bias=False),
		    nn.ReLU6(inplace=True),
		    # pw-linear
		    nn.Conv2d(channels*2, channels, 1, 1, 0, 1, 1, bias=False)
        )

        self.conv1 = nn.Sequential(
	
			nn.Conv2d(channels, channels, kernel_size=3, padding=dilation, dilation=dilation, groups=channels,
					  bias=False),
			nn.ReLU6(inplace=True),
			# pw-linear
			nn.Conv2d(channels, channels, 1, 1, 0, 1, 1, bias=False)
		)


    def forward(self, x):
        res = self.conv1(self.conv0(x))
        return res + x


class DilatedResidualBlock(nn.Module):
    def __init__(self, channels, dilation):
        super(DilatedResidualBlock, self).__init__()
        self.conv0 = nn.Sequential(
            nn.Conv2d(channels, channels, kernel_size=3, padding=dilation, dilation=dilation), nn.ReLU()
        )
        self.conv1 = nn.Conv2d(channels, channels, kernel_size=3, padding=dilation, dilation=dilation)

    def forward(self, x):
        conv0 = self.conv0(x)
        conv1 = self.conv1(conv0)
        return x + conv1


class SpatialRNN(nn.Module):
	"""
	SpatialRNN model for one direction only
	"""
	def __init__(self, alpha = 1.0, channel_num = 1, direction = "right"):
		super(SpatialRNN, self).__init__()
		self.alpha = nn.Parameter(torch.Tensor([alpha] * channel_num))
		self.direction = direction

	def __getitem__(self, item):
		return self.alpha[item]

	def __len__(self):
		return len(self.alpha)


	def forward(self, x):
		"""
		:param x: (N,C,H,W)
		:return:
		"""
		height = x.size(2)
		weight = x.size(3)
		x_out = []

		# from left to right
		if self.direction == "right":
			x_out = [x[:, :, :, 0].clamp(min=0)]

			for i in range(1, weight):
				temp = (self.alpha.unsqueeze(1) * x_out[i - 1] + x[:, :, :, i]).clamp(min=0)
				x_out.append(temp)  # a list of tensor

			return torch.stack(x_out, 3)  # merge into one tensor

		# from right to left
		elif self.direction == "left":
			x_out = [x[:, :, :, -1].clamp(min=0)]

			for i in range(1, weight):
				temp = (self.alpha.unsqueeze(1) * x_out[i - 1] + x[:, :, :, -i - 1]).clamp(min=0)
				x_out.append(temp)

			x_out.reverse()
			return torch.stack(x_out, 3)

		# from up to down
		elif self.direction == "down":
			x_out = [x[:, :, 0, :].clamp(min=0)]

			for i in range(1, height):
				temp = (self.alpha.unsqueeze(1) * x_out[i - 1] + x[:, :, i, :]).clamp(min=0)
				x_out.append(temp)

			return torch.stack(x_out, 2)

		# from down to up
		elif self.direction == "up":
			x_out = [x[:, :, -1, :].clamp(min=0)]

			for i in range(1, height):
				temp = (self.alpha.unsqueeze(1) * x_out[i - 1] + x[:, :, -i - 1, :]).clamp(min=0)
				x_out.append(temp)

			x_out.reverse()
			return torch.stack(x_out, 2)

		else:
			print("Invalid direction in SpatialRNN!")
			return KeyError



class TVLoss(nn.Module):
    def __init__(self, tv_loss_weight=1):
        super(TVLoss, self).__init__()
        self.tv_loss_weight = tv_loss_weight

    def forward(self, x):
        batch_size = x.size()[0]
        h_x = x.size()[2]
        w_x = x.size()[3]
        count_h = self.tensor_size(x[:, :, 1:, :])
        count_w = self.tensor_size(x[:, :, :, 1:])
        h_tv = torch.pow((x[:, :, 1:, :] - x[:, :, :h_x - 1, :]), 2).sum()
        w_tv = torch.pow((x[:, :, :, 1:] - x[:, :, :, :w_x - 1]), 2).sum()
        return self.tv_loss_weight * 2 * (h_tv / count_h + w_tv / count_w) / batch_size

    @staticmethod
    def tensor_size(t):
        return t.size()[1] * t.size()[2] * t.size()[3]


class NLB(nn.Module):
    def __init__(self, in_channels):
        super(NLB, self).__init__()
        self.theta = nn.Conv2d(in_channels, int(in_channels / 2), kernel_size=1)
        self.phi = nn.Conv2d(in_channels, int(in_channels / 2), kernel_size=1)
        self.g = nn.Conv2d(in_channels, int(in_channels / 2), kernel_size=1)

        self.down = nn.Conv2d(in_channels, in_channels, kernel_size=4, stride=4, groups=in_channels, bias=False)
        self.down.weight.data.fill_(1. / 16)

        self.z = nn.Conv2d(int(in_channels / 2), in_channels, kernel_size=1)

    def forward(self, x):
        n, c, h, w = x.size()
        x_down = self.down(x)

        # [n, (h / 4) * (w / 4), c / 2]
        theta = self.theta(x_down).view(n, int(c / 2), -1).transpose(1, 2)
        # [n, c / 2, (h / 8) * (w / 8)]
        phi = F.max_pool2d(self.phi(x_down), kernel_size=2, stride=2).view(n, int(c / 2), -1)
        # [n, (h / 8) * (w / 8), c / 2]
        g = F.max_pool2d(self.g(x_down), kernel_size=2, stride=2).view(n, int(c / 2), -1).transpose(1, 2)
        # [n, (h / 4) * (w / 4), (h / 8) * (w / 8)]
        f = F.softmax(torch.bmm(theta, phi), 2)
        # [n, c / 2, h / 4, w / 4]
        y = torch.bmm(f, g).transpose(1, 2).contiguous().view(n, int(c / 2), int(h / 4), int(w / 4))

        return x + F.upsample(self.z(y), size=x.size()[2:], mode='bilinear', align_corners=True)

In [12]:
class DGNLNet_fast(nn.Module):
    def __init__(self, num_features=64):
        super(DGNLNet_fast, self).__init__()
        self.mean = torch.zeros(1, 3, 1, 1)
        self.std = torch.zeros(1, 3, 1, 1)
        self.mean[0, 0, 0, 0] = 0.485
        self.mean[0, 1, 0, 0] = 0.456
        self.mean[0, 2, 0, 0] = 0.406
        self.std[0, 0, 0, 0] = 0.229
        self.std[0, 1, 0, 0] = 0.224
        self.std[0, 2, 0, 0] = 0.225

        self.mean = nn.Parameter(self.mean)
        self.std = nn.Parameter(self.std)
        self.mean.requires_grad = False
        self.std.requires_grad = False

        ############################################ Depth prediction network
        self.conv1 = nn.Sequential(
			nn.Conv2d(3, 32, 8, stride=4, padding=2),
			nn.GroupNorm(num_groups=32, num_channels=32),
			nn.SELU(inplace=True)
		)

        self.conv2 = nn.Sequential(
			nn.Conv2d(32, 64, 4, stride=2, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=64),
			nn.SELU(inplace=True)
		)

        self.conv3 = nn.Sequential(
			nn.Conv2d(64, 128, 4, stride=2, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=128),
			nn.SELU(inplace=True)
		)

        self.conv5 = nn.Sequential(
			nn.Conv2d(128, 128, 3, padding=2, dilation=2),
			nn.GroupNorm(num_groups=32, num_channels=128),
			nn.SELU(inplace=True)
		)

        self.conv8 = nn.Sequential(
			nn.ConvTranspose2d(128, 64, kernel_size=4, stride=2, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=64),
			nn.SELU(inplace=True)
		)

        self.conv9 = nn.Sequential(
			nn.ConvTranspose2d(64, 32, kernel_size=4, stride=2, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=32),
			nn.SELU(inplace=True)
		)


        self.depth_pred = nn.Sequential(
			nn.Conv2d(32, 32, kernel_size=3, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=32),
			nn.SELU(inplace=True),
			nn.Conv2d(32, 1, kernel_size=1, stride=1, padding=0),
			nn.Sigmoid()
		)

	############################################ Rain removal network


        self.head = nn.Sequential(
			# pw
			nn.Conv2d(3, 32, 1, 1, 0, 1, bias=False),
			nn.ReLU6(inplace=True),
			# dw
			nn.Conv2d(32, 32, kernel_size=8, stride=4, padding=2, groups=32, bias=False),
			nn.ReLU6(inplace=True),
			# pw-linear
			nn.Conv2d(32, num_features, 1, 1, 0, 1, 1, bias=False),
		)

        self.body = nn.Sequential(
			DepthWiseDilatedResidualBlock(num_features, num_features, 1),
			# DepthWiseDilatedResidualBlock(num_features, num_features, 1),
			DepthWiseDilatedResidualBlock(num_features, num_features, 2),
			DepthWiseDilatedResidualBlock(num_features, num_features, 2),
			DepthWiseDilatedResidualBlock(num_features, num_features, 4),
			DepthWiseDilatedResidualBlock(num_features, num_features, 8),
			DepthWiseDilatedResidualBlock(num_features, num_features, 4),
			DepthWiseDilatedResidualBlock(num_features, num_features, 2),
			DepthWiseDilatedResidualBlock(num_features, num_features, 2),
			# DepthWiseDilatedResidualBlock(num_features, num_features, 1),
			DepthWiseDilatedResidualBlock(num_features, num_features, 1)
		)


        self.dgnlb = DGNL(num_features)


        self.tail = nn.Sequential(
			# dw
			nn.ConvTranspose2d(num_features, 32, kernel_size=8, stride=4, padding=2, groups=32, bias=False),
			nn.ReLU6(inplace=True),
			# pw-linear
			nn.Conv2d(32, 3, 1, 1, 0, 1, bias=False),
		)

        for m in self.modules():
            if isinstance(m, nn.ReLU):
                m.inplace = True

    def forward(self, x):
        x = (x - self.mean) / self.std

        ################################## depth prediction
        d_f1 = self.conv1(x)
        d_f2 = self.conv2(d_f1)
        d_f3 = self.conv3(d_f2)
        d_f5 = self.conv5(d_f3)
        d_f8 = self.conv8(d_f5)
        d_f9 = self.conv9(d_f8 + d_f2)
        depth_pred = self.depth_pred(d_f9 + d_f1)

        ################################## rain removal

        f = self.head(x)
        f = self.body(f)
        f = self.dgnlb(f, depth_pred.detach())
        r = self.tail(f)
        x = x + r

        x = (x * self.std + self.mean).clamp(min=0, max=1)

        if self.training:
            return x, F.upsample(depth_pred, size=x.size()[2:], mode='bilinear', align_corners=True)

        return x



class DGNLNet(nn.Module):
    def __init__(self, num_features=64):
        super(DGNLNet, self).__init__()
        self.mean = torch.zeros(1, 3, 1, 1)
        self.std = torch.zeros(1, 3, 1, 1)
        self.mean[0, 0, 0, 0] = 0.485
        self.mean[0, 1, 0, 0] = 0.456
        self.mean[0, 2, 0, 0] = 0.406
        self.std[0, 0, 0, 0] = 0.229
        self.std[0, 1, 0, 0] = 0.224
        self.std[0, 2, 0, 0] = 0.225

        self.mean = nn.Parameter(self.mean)
        self.std = nn.Parameter(self.std)
        self.mean.requires_grad = False
        self.std.requires_grad = False

        ############################################ Depth prediction network
        self.conv1 = nn.Sequential(
			nn.Conv2d(3, 32, 4, stride=2, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=32),
			nn.SELU(inplace=True)
		)

        self.conv2 = nn.Sequential(
			nn.Conv2d(32, 64, 4, stride=2, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=64),
			nn.SELU(inplace=True)
		)

        self.conv3 = nn.Sequential(
			nn.Conv2d(64, 128, 4, stride=2, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=128),
			nn.SELU(inplace=True)
		)

        self.conv4 = nn.Sequential(
			nn.Conv2d(128, 256, 4, stride=2, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=256),
			nn.SELU(inplace=True)
		)

        self.conv5 = nn.Sequential(
			nn.Conv2d(256, 256, 3, padding=2, dilation=2),
			nn.GroupNorm(num_groups=32, num_channels=256),
			nn.SELU(inplace=True)
		)

        self.conv6 = nn.Sequential(
			nn.Conv2d(256, 256, 3, padding=4, dilation=4),
			nn.GroupNorm(num_groups=32, num_channels=256),
			nn.SELU(inplace=True)
		)

        self.conv7 = nn.Sequential(
			nn.Conv2d(256, 256, 3, padding=2, dilation=2),
			nn.GroupNorm(num_groups=32, num_channels=256),
			nn.SELU(inplace=True)
		)

        self.conv8 = nn.Sequential(
			nn.ConvTranspose2d(256, 128, kernel_size=4, stride=2, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=128),
			nn.SELU(inplace=True)
		)

        self.conv9 = nn.Sequential(
			nn.ConvTranspose2d(128, 64, kernel_size=4, stride=2, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=64),
			nn.SELU(inplace=True)
		)

        self.conv10 = nn.Sequential(
			nn.ConvTranspose2d(64, 32, kernel_size=4, stride=2, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=32),
			nn.SELU(inplace=True)
		)

        self.depth_pred = nn.Sequential(
			nn.ConvTranspose2d(32, 32, kernel_size=4, stride=2, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=32),
			nn.SELU(inplace=True),
			nn.Conv2d(32, 32, kernel_size=3, padding=1),
			nn.SELU(inplace=True),
			nn.Conv2d(32, 1, kernel_size=1, stride=1, padding=0),
			nn.Sigmoid()
		)

	############################################ Rain removal network

        self.head = nn.Sequential(
            nn.Conv2d(3, 32, kernel_size=4, stride=2, padding=1), nn.ReLU(),
            nn.Conv2d(32, num_features, kernel_size=1, stride=1, padding=0), nn.ReLU()
        )
        self.body = nn.Sequential(
            DilatedResidualBlock(num_features, 1),
            DilatedResidualBlock(num_features, 1),
            DilatedResidualBlock(num_features, 2),
            DilatedResidualBlock(num_features, 2),
            DilatedResidualBlock(num_features, 4),
            DilatedResidualBlock(num_features, 8),
            DilatedResidualBlock(num_features, 4),
            DilatedResidualBlock(num_features, 2),
            DilatedResidualBlock(num_features, 2),
            DilatedResidualBlock(num_features, 1),
            DilatedResidualBlock(num_features, 1)
        )

        self.dgnlb = DGNL(num_features)

        self.tail = nn.Sequential(
            # nn.Conv2d(num_features, num_features, kernel_size=3, padding=1), nn.ReLU(),
            nn.ConvTranspose2d(num_features, 32, kernel_size=4, stride=2, padding=1), nn.ReLU(),
            nn.Conv2d(32, 3, kernel_size=3, padding=1)
        )

        for m in self.modules():
            if isinstance(m, nn.ReLU):
                m.inplace = True

    def forward(self, x):
        x = (x - self.mean) / self.std

        ################################## depth prediction
        d_f1 = self.conv1(x)
        d_f2 = self.conv2(d_f1)
        d_f3 = self.conv3(d_f2)
        d_f4 = self.conv4(d_f3)
        d_f5 = self.conv5(d_f4)
        d_f6 = self.conv6(d_f5)
        d_f7 = self.conv7(d_f6)
        d_f8 = self.conv8(d_f7)
        d_f9 = self.conv9(d_f8 + d_f3)
        d_f10 = self.conv10(d_f9 + d_f2)
        depth_pred = self.depth_pred(d_f10 + d_f1)

        ################################## rain removal

        f = self.head(x)
        f = self.body(f)
        f = self.dgnlb(f, depth_pred.detach())
        r = self.tail(f)
        x = x + r

        x = (x * self.std + self.mean).clamp(min=0, max=1)

        if self.training:
            return x, depth_pred

        return x


class basic_NL(nn.Module):
    def __init__(self, num_features=64):
        super(basic_NL, self).__init__()
        self.mean = torch.zeros(1, 3, 1, 1)
        self.std = torch.zeros(1, 3, 1, 1)
        self.mean[0, 0, 0, 0] = 0.485
        self.mean[0, 1, 0, 0] = 0.456
        self.mean[0, 2, 0, 0] = 0.406
        self.std[0, 0, 0, 0] = 0.229
        self.std[0, 1, 0, 0] = 0.224
        self.std[0, 2, 0, 0] = 0.225

        self.mean = nn.Parameter(self.mean)
        self.std = nn.Parameter(self.std)
        self.mean.requires_grad = False
        self.std.requires_grad = False

        self.head = nn.Sequential(
            nn.Conv2d(3, 32, kernel_size=4, stride=2, padding=1), nn.ReLU(),
            nn.Conv2d(32, num_features, kernel_size=1, stride=1, padding=0), nn.ReLU()
        )
        self.body = nn.Sequential(
            DilatedResidualBlock(num_features, 1),
            DilatedResidualBlock(num_features, 1),
            DilatedResidualBlock(num_features, 2),
            DilatedResidualBlock(num_features, 2),
            DilatedResidualBlock(num_features, 4),
            DilatedResidualBlock(num_features, 8),
            DilatedResidualBlock(num_features, 4),
            DilatedResidualBlock(num_features, 2),
            DilatedResidualBlock(num_features, 2),
            DilatedResidualBlock(num_features, 1),
            DilatedResidualBlock(num_features, 1)
        )

        self.nlb = NLB(num_features)

        self.tail = nn.Sequential(
            # nn.Conv2d(num_features, num_features, kernel_size=3, padding=1), nn.ReLU(),
            nn.ConvTranspose2d(num_features, 32, kernel_size=4, stride=2, padding=1), nn.ReLU(),
            nn.Conv2d(32, 3, kernel_size=3, padding=1)
        )

        for m in self.modules():
            if isinstance(m, nn.ReLU):
                m.inplace = True

    def forward(self, x):
        x = (x - self.mean) / self.std

        f = self.head(x)
        f = self.body(f)
        f = self.nlb(f)
        r = self.tail(f)
        x = x + r

        x = (x * self.std + self.mean).clamp(min=0, max=1)
        return x



class basic(nn.Module):
    def __init__(self, num_features=64):
        super(basic, self).__init__()
        self.mean = torch.zeros(1, 3, 1, 1)
        self.std = torch.zeros(1, 3, 1, 1)
        self.mean[0, 0, 0, 0] = 0.485
        self.mean[0, 1, 0, 0] = 0.456
        self.mean[0, 2, 0, 0] = 0.406
        self.std[0, 0, 0, 0] = 0.229
        self.std[0, 1, 0, 0] = 0.224
        self.std[0, 2, 0, 0] = 0.225

        self.mean = nn.Parameter(self.mean)
        self.std = nn.Parameter(self.std)
        self.mean.requires_grad = False
        self.std.requires_grad = False

        self.head = nn.Sequential(
            nn.Conv2d(3, 32, kernel_size=4, stride = 2 ,padding=1), nn.ReLU(),
			nn.Conv2d(32, num_features, kernel_size=1, stride=1, padding=0), nn.ReLU()
        )
        self.body = nn.Sequential(
            DilatedResidualBlock(num_features, 1),
            DilatedResidualBlock(num_features, 1),
            DilatedResidualBlock(num_features, 2),
            DilatedResidualBlock(num_features, 2),
            DilatedResidualBlock(num_features, 4),
            DilatedResidualBlock(num_features, 8),
            DilatedResidualBlock(num_features, 4),
            DilatedResidualBlock(num_features, 2),
            DilatedResidualBlock(num_features, 2),
            DilatedResidualBlock(num_features, 1),
            DilatedResidualBlock(num_features, 1)
        )

        self.tail = nn.Sequential(
            #nn.Conv2d(num_features, num_features, kernel_size=3, padding=1), nn.ReLU(),
            nn.ConvTranspose2d(num_features, 32, kernel_size=4, stride=2, padding=1), nn.ReLU(),
            nn.Conv2d(32, 3, kernel_size=3, padding=1)
        )

        for m in self.modules():
            if isinstance(m, nn.ReLU):
                m.inplace = True

    def forward(self, x):
        x = (x - self.mean) / self.std

        f = self.head(x)
        f = self.body(f)
        r = self.tail(f)
        x = x + r

        x = (x * self.std + self.mean).clamp(min=0, max=1)
        return x



class depth_predciton(nn.Module):
    def __init__(self):
        super(depth_predciton, self).__init__()
        self.mean = torch.zeros(1, 3, 1, 1)
        self.std = torch.zeros(1, 3, 1, 1)
        self.mean[0, 0, 0, 0] = 0.485
        self.mean[0, 1, 0, 0] = 0.456
        self.mean[0, 2, 0, 0] = 0.406
        self.std[0, 0, 0, 0] = 0.229
        self.std[0, 1, 0, 0] = 0.224
        self.std[0, 2, 0, 0] = 0.225

        self.mean = nn.Parameter(self.mean)
        self.std = nn.Parameter(self.std)
        self.mean.requires_grad = False
        self.std.requires_grad = False


        self.conv1 = nn.Sequential(
            nn.Conv2d(3, 32, 4, stride=2, padding=1),
            nn.GroupNorm(num_groups=32, num_channels=32),
            nn.SELU(inplace=True)
        )

        self.conv2 = nn.Sequential(
            nn.Conv2d(32, 64, 4, stride=2, padding=1),
            nn.GroupNorm(num_groups=32, num_channels=64),
            nn.SELU(inplace=True)
        )

        self.conv3 = nn.Sequential(
            nn.Conv2d(64, 128, 4, stride=2, padding=1),
            nn.GroupNorm(num_groups=32, num_channels=128),
            nn.SELU(inplace=True)
        )

        self.conv4 = nn.Sequential(
            nn.Conv2d(128, 256, 4, stride=2, padding=1),
            nn.GroupNorm(num_groups=32, num_channels=256),
            nn.SELU(inplace=True)
        )

        self.conv5 = nn.Sequential(
            nn.Conv2d(256, 256, 3, padding=2, dilation=2),
            nn.GroupNorm(num_groups=32, num_channels=256),
            nn.SELU(inplace=True)
        )

        self.conv6 = nn.Sequential(
            nn.Conv2d(256, 256, 3, padding=4, dilation=4),
            nn.GroupNorm(num_groups=32, num_channels=256),
            nn.SELU(inplace=True)
        )

        self.conv7 = nn.Sequential(
            nn.Conv2d(256, 256, 3, padding=2, dilation=2),
            nn.GroupNorm(num_groups=32, num_channels=256),
            nn.SELU(inplace=True)
        )

        self.conv8 = nn.Sequential(
            nn.ConvTranspose2d(256, 128, kernel_size=4, stride=2, padding=1),
            nn.GroupNorm(num_groups=32, num_channels=128),
            nn.SELU(inplace=True)
        )

        self.conv9 = nn.Sequential(
            nn.ConvTranspose2d(128, 64, kernel_size=4, stride=2, padding=1),
            nn.GroupNorm(num_groups=32, num_channels=64),
            nn.SELU(inplace=True)
        )

        self.conv10 = nn.Sequential(
            nn.ConvTranspose2d(64, 32, kernel_size=4, stride=2, padding=1),
            nn.GroupNorm(num_groups=32, num_channels=32),
            nn.SELU(inplace=True)
        )

        self.depth_pred = nn.Sequential(
            nn.ConvTranspose2d(32, 32, kernel_size=4, stride=2, padding=1),
            nn.GroupNorm(num_groups=32, num_channels=32),
            nn.SELU(inplace=True),
            nn.Conv2d(32, 32, kernel_size=3, padding=1), nn.SELU(inplace=True),
            nn.Conv2d(32, 1, kernel_size=1, stride=1, padding=0),
            nn.Sigmoid()
        )


    def forward(self, x):

        x = (x - self.mean) / self.std

        d_f1 = self.conv1(x)
        d_f2 = self.conv2(d_f1)
        d_f3 = self.conv3(d_f2)
        d_f4 = self.conv4(d_f3)
        d_f5 = self.conv5(d_f4)
        d_f6 = self.conv6(d_f5)
        d_f7 = self.conv7(d_f6)
        d_f8 = self.conv8(d_f7)
        d_f9 = self.conv9(d_f8+d_f3)
        d_f10 = self.conv10(d_f9+d_f2)
        depth_pred = self.depth_pred(d_f10+d_f1)


        return depth_pred

In [13]:
def main():
    net = DGNLNet().cuda().train()
    net = nn.DataParallel(net)
    net.to(torch.device("cuda"))
    torch.cuda.empty_cache()

    optimizer = optim.Adam([
        {'params': [param for name, param in net.named_parameters() if name[-4:] == 'bias' and param.requires_grad],
         'lr': 2 * args['lr']},
        {'params': [param for name, param in net.named_parameters() if name[-4:] != 'bias' and param.requires_grad],
         'lr': args['lr'], 'weight_decay': args['weight_decay']}
    ])

    if len(args['resume_snapshot']) > 0:
        print('training resumes from \'%s\'' % args['resume_snapshot'])
        net.load_state_dict(torch.load(os.path.join(ckpt_path, exp_name, args['resume_snapshot'] + '.pth')))
        optimizer.load_state_dict(torch.load(os.path.join(ckpt_path, exp_name, args['resume_snapshot'] + '_optim.pth')))
        optimizer.param_groups[0]['lr'] = 2 * args['lr']
        optimizer.param_groups[1]['lr'] = args['lr']

    check_mkdir(ckpt_path)
    check_mkdir(os.path.join(ckpt_path, exp_name))
    open(log_path, 'w').write(str(args) + '\n\n')
    train(net, optimizer)

In [14]:
def train(net, optimizer):
    curr_iter = args['last_iter']
    while True:
        train_loss_record = AvgMeter()
        train_net_loss_record = AvgMeter()
        train_depth_loss_record = AvgMeter()

        for i, data in enumerate(train_loader):
            optimizer.param_groups[0]['lr'] = 2 * args['lr'] * (1 - float(curr_iter) / args['iter_num']
                                                                ) ** args['lr_decay']
            optimizer.param_groups[1]['lr'] = args['lr'] * (1 - float(curr_iter) / args['iter_num']
                                                            ) ** args['lr_decay']

            inputs, gts, dps = data
            batch_size = inputs.size(0)
            inputs = Variable(inputs).cuda()
            gts = Variable(gts).cuda()
            dps = Variable(dps).cuda()

            optimizer.zero_grad()

            result, depth_pred = net(inputs)

            loss_net = criterion(result, gts)
            loss_depth = criterion_depth(depth_pred, dps)

            loss = loss_net + loss_depth

            loss.backward()

            optimizer.step()

            train_loss_record.update(loss.data, batch_size)
            train_net_loss_record.update(loss_net.data, batch_size)
            train_depth_loss_record.update(loss_depth.data, batch_size)

            curr_iter += 1

            log = '[iter %d], [train loss %.5f], [lr %.13f], [loss_net %.5f], [loss_depth %.5f]' % \
                  (curr_iter, train_loss_record.avg, optimizer.param_groups[1]['lr'],
                   train_net_loss_record.avg, train_depth_loss_record.avg)
            print(log)
            open(log_path, 'a').write(log + '\n')

            if (curr_iter + 1) % args['val_freq'] == 0:
                validate(net, curr_iter, optimizer)

            if (curr_iter + 1) % args['snapshot_epochs'] == 0:
                torch.save(net.state_dict(), os.path.join(ckpt_path, exp_name, ('%d_test.pth' % (curr_iter + 1) )))
                torch.save(optimizer.state_dict(), os.path.join(ckpt_path, exp_name, ('%d_optim_test.pth' % (curr_iter + 1) )))

            if curr_iter > args['iter_num']:
                return

In [15]:
def validate(net, curr_iter, optimizer):
    print('validating...')
    net.eval()

    loss_record1, loss_record2 = AvgMeter(), AvgMeter()
    iter_num1 = len(test1_loader)

    with torch.no_grad():
        for i, data in enumerate(test1_loader):
            inputs, gts, dps = data
            inputs = Variable(inputs).cuda()
            gts = Variable(gts).cuda()
            dps = Variable(dps).cuda()

            res = net(inputs)

            loss = criterion(res, gts)
            loss_record1.update(loss.data, inputs.size(0))

            print('processed test1 %d / %d' % (i + 1, iter_num1))


    snapshot_name = 'iter_%d_loss1_%.5f_loss2_%.5f_lr_%.6f' % (curr_iter + 1, loss_record1.avg, loss_record2.avg,
                                                               optimizer.param_groups[1]['lr'])
    print('[validate]: [iter %d], [loss1 %.5f], [loss2 %.5f]' % (curr_iter + 1, loss_record1.avg, loss_record2.avg))
    torch.save(net.state_dict(), os.path.join(ckpt_path, exp_name, snapshot_name + '.pth'))
    torch.save(optimizer.state_dict(), os.path.join(ckpt_path, exp_name, snapshot_name + '_optim.pth'))

    net.train()

In [16]:
import os
os.environ['CUDA_VISIBLE_DEVICES'] = '1, 2, 3'
print(os.environ['CUDA_VISIBLE_DEVICES'])
print(torch.cuda.is_available())


1, 2, 3
True


In [17]:
main()

/home/gregory/.local/lib/python3.7/site-packages/ipykernel_launcher.py:19: DeprecationWarning: BILINEAR is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.BILINEAR instead.
/home/gregory/.local/lib/python3.7/site-packages/ipykernel_launcher.py:19: DeprecationWarning: BILINEAR is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.BILINEAR instead.
/home/gregory/.local/lib/python3.7/site-packages/ipykernel_launcher.py:19: DeprecationWarning: BILINEAR is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.BILINEAR instead.
/home/gregory/.local/lib/python3.7/site-packages/ipykernel_launcher.py:19: DeprecationWarning: BILINEAR is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.BILINEAR instead.
/home/gregory/.local/lib/python3.7/site-packages/ipykernel_launcher.py:39: DeprecationWarning: FLIP_LEFT_RIGHT is deprecated and will be removed in Pillow 10 (2023-07-01). Use Transpose.FLIP_LEFT_RIGHT instea

[iter 1], [train loss 0.54836], [lr 0.0005000000000], [loss_net 0.15366], [loss_depth 0.39469]
[iter 2], [train loss 0.51721], [lr 0.0004999887500], [loss_net 0.12100], [loss_depth 0.39621]
[iter 3], [train loss 0.50090], [lr 0.0004999774999], [loss_net 0.11393], [loss_depth 0.38696]
[iter 4], [train loss 0.49873], [lr 0.0004999662499], [loss_net 0.11926], [loss_depth 0.37947]
[iter 5], [train loss 0.47788], [lr 0.0004999549998], [loss_net 0.11236], [loss_depth 0.36552]
[iter 6], [train loss 0.46656], [lr 0.0004999437496], [loss_net 0.10622], [loss_depth 0.36034]
[iter 7], [train loss 0.45470], [lr 0.0004999324995], [loss_net 0.10785], [loss_depth 0.34685]
[iter 8], [train loss 0.44876], [lr 0.0004999212493], [loss_net 0.11095], [loss_depth 0.33781]
[iter 9], [train loss 0.45040], [lr 0.0004999099991], [loss_net 0.11294], [loss_depth 0.33746]
[iter 10], [train loss 0.44232], [lr 0.0004998987489], [loss_net 0.10893], [loss_depth 0.33339]
[iter 11], [train loss 0.43712], [lr 0.0004998874

[iter 87], [train loss 0.30960], [lr 0.0004990323959], [loss_net 0.09238], [loss_depth 0.21721]
[iter 88], [train loss 0.30852], [lr 0.0004990211435], [loss_net 0.09202], [loss_depth 0.21650]
[iter 89], [train loss 0.30861], [lr 0.0004990098910], [loss_net 0.09199], [loss_depth 0.21662]
[iter 90], [train loss 0.30936], [lr 0.0004989986385], [loss_net 0.09228], [loss_depth 0.21708]
[iter 91], [train loss 0.30927], [lr 0.0004989873860], [loss_net 0.09176], [loss_depth 0.21751]
[iter 92], [train loss 0.30914], [lr 0.0004989761335], [loss_net 0.09172], [loss_depth 0.21743]
[iter 93], [train loss 0.30847], [lr 0.0004989648809], [loss_net 0.09141], [loss_depth 0.21706]
[iter 94], [train loss 0.30798], [lr 0.0004989536283], [loss_net 0.09114], [loss_depth 0.21684]
[iter 95], [train loss 0.30762], [lr 0.0004989423756], [loss_net 0.09075], [loss_depth 0.21687]
[iter 96], [train loss 0.30733], [lr 0.0004989311230], [loss_net 0.09071], [loss_depth 0.21662]
[iter 97], [train loss 0.30641], [lr 0.0

[iter 172], [train loss 0.27277], [lr 0.0004980758382], [loss_net 0.08570], [loss_depth 0.18708]
[iter 173], [train loss 0.27276], [lr 0.0004980645833], [loss_net 0.08571], [loss_depth 0.18705]
[iter 174], [train loss 0.27261], [lr 0.0004980533285], [loss_net 0.08568], [loss_depth 0.18693]
[iter 175], [train loss 0.27269], [lr 0.0004980420736], [loss_net 0.08553], [loss_depth 0.18717]
[iter 176], [train loss 0.27232], [lr 0.0004980308186], [loss_net 0.08548], [loss_depth 0.18684]
[iter 177], [train loss 0.27161], [lr 0.0004980195637], [loss_net 0.08538], [loss_depth 0.18623]
[iter 178], [train loss 0.27095], [lr 0.0004980083087], [loss_net 0.08530], [loss_depth 0.18565]
[iter 179], [train loss 0.27082], [lr 0.0004979970537], [loss_net 0.08538], [loss_depth 0.18545]
[iter 180], [train loss 0.27105], [lr 0.0004979857987], [loss_net 0.08556], [loss_depth 0.18550]
[iter 181], [train loss 0.27142], [lr 0.0004979745436], [loss_net 0.08544], [loss_depth 0.18598]
[iter 182], [train loss 0.2712

[iter 257], [train loss 0.25127], [lr 0.0004971190762], [loss_net 0.08131], [loss_depth 0.16997]
[iter 258], [train loss 0.25091], [lr 0.0004971078190], [loss_net 0.08122], [loss_depth 0.16969]
[iter 259], [train loss 0.25064], [lr 0.0004970965617], [loss_net 0.08114], [loss_depth 0.16950]
[iter 260], [train loss 0.25061], [lr 0.0004970853044], [loss_net 0.08119], [loss_depth 0.16942]
[iter 261], [train loss 0.25015], [lr 0.0004970740471], [loss_net 0.08108], [loss_depth 0.16908]
[iter 262], [train loss 0.24991], [lr 0.0004970627897], [loss_net 0.08105], [loss_depth 0.16886]
[iter 263], [train loss 0.25039], [lr 0.0004970515324], [loss_net 0.08128], [loss_depth 0.16911]
[iter 264], [train loss 0.25031], [lr 0.0004970402750], [loss_net 0.08115], [loss_depth 0.16916]
[iter 265], [train loss 0.25003], [lr 0.0004970290175], [loss_net 0.08109], [loss_depth 0.16894]
[iter 266], [train loss 0.24951], [lr 0.0004970177601], [loss_net 0.08099], [loss_depth 0.16852]
[iter 267], [train loss 0.2489

...

[iter 39913], [train loss 0.03550], [lr 0.0000020283851], [loss_net 0.01826], [loss_depth 0.01724]
[iter 39914], [train loss 0.03549], [lr 0.0000020076284], [loss_net 0.01825], [loss_depth 0.01724]
[iter 39915], [train loss 0.03549], [lr 0.0000019868479], [loss_net 0.01825], [loss_depth 0.01724]
[iter 39916], [train loss 0.03549], [lr 0.0000019660431], [loss_net 0.01825], [loss_depth 0.01724]
[iter 39917], [train loss 0.03549], [lr 0.0000019452139], [loss_net 0.01825], [loss_depth 0.01724]
[iter 39918], [train loss 0.03549], [lr 0.0000019243599], [loss_net 0.01825], [loss_depth 0.01724]
[iter 39919], [train loss 0.03550], [lr 0.0000019034807], [loss_net 0.01826], [loss_depth 0.01724]
[iter 39920], [train loss 0.03550], [lr 0.0000018825760], [loss_net 0.01826], [loss_depth 0.01724]
[iter 39921], [train loss 0.03550], [lr 0.0000018616456], [loss_net 0.01826], [loss_depth 0.01724]
[iter 39922], [train loss 0.03549], [lr 0.0000018406889], [loss_net 0.01825], [loss_depth 0.01724]
[iter 3992

[iter 39996], [train loss 0.03543], [lr 0.0000001535285], [loss_net 0.01824], [loss_depth 0.01719]
[iter 39997], [train loss 0.03543], [lr 0.0000001255943], [loss_net 0.01823], [loss_depth 0.01719]
[iter 39998], [train loss 0.03542], [lr 0.0000000969449], [loss_net 0.01823], [loss_depth 0.01719]
[iter 39999], [train loss 0.03542], [lr 0.0000000673043], [loss_net 0.01823], [loss_depth 0.01719]
validating...
processed test1 1 / 1094
processed test1 2 / 1094
processed test1 3 / 1094
processed test1 4 / 1094
processed test1 5 / 1094
processed test1 6 / 1094
processed test1 7 / 1094
processed test1 8 / 1094
processed test1 9 / 1094
processed test1 10 / 1094
processed test1 11 / 1094
processed test1 12 / 1094
processed test1 13 / 1094
processed test1 14 / 1094
processed test1 15 / 1094
processed test1 16 / 1094
processed test1 17 / 1094
processed test1 18 / 1094
processed test1 19 / 1094
processed test1 20 / 1094
processed test1 21 / 1094
processed test1 22 / 1094
processed test1 23 / 1094
p

processed test1 294 / 1094
processed test1 295 / 1094
processed test1 296 / 1094
processed test1 297 / 1094
processed test1 298 / 1094
processed test1 299 / 1094
processed test1 300 / 1094
processed test1 301 / 1094
processed test1 302 / 1094
processed test1 303 / 1094
processed test1 304 / 1094
processed test1 305 / 1094
processed test1 306 / 1094
processed test1 307 / 1094
processed test1 308 / 1094
processed test1 309 / 1094
processed test1 310 / 1094
processed test1 311 / 1094
processed test1 312 / 1094
processed test1 313 / 1094
processed test1 314 / 1094
processed test1 315 / 1094
processed test1 316 / 1094
processed test1 317 / 1094
processed test1 318 / 1094
processed test1 319 / 1094
processed test1 320 / 1094
processed test1 321 / 1094
processed test1 322 / 1094
processed test1 323 / 1094
processed test1 324 / 1094
processed test1 325 / 1094
processed test1 326 / 1094
processed test1 327 / 1094
processed test1 328 / 1094
processed test1 329 / 1094
processed test1 330 / 1094
p

processed test1 598 / 1094
processed test1 599 / 1094
processed test1 600 / 1094
processed test1 601 / 1094
processed test1 602 / 1094
processed test1 603 / 1094
processed test1 604 / 1094
processed test1 605 / 1094
processed test1 606 / 1094
processed test1 607 / 1094
processed test1 608 / 1094
processed test1 609 / 1094
processed test1 610 / 1094
processed test1 611 / 1094
processed test1 612 / 1094
processed test1 613 / 1094
processed test1 614 / 1094
processed test1 615 / 1094
processed test1 616 / 1094
processed test1 617 / 1094
processed test1 618 / 1094
processed test1 619 / 1094
processed test1 620 / 1094
processed test1 621 / 1094
processed test1 622 / 1094
processed test1 623 / 1094
processed test1 624 / 1094
processed test1 625 / 1094
processed test1 626 / 1094
processed test1 627 / 1094
processed test1 628 / 1094
processed test1 629 / 1094
processed test1 630 / 1094
processed test1 631 / 1094
processed test1 632 / 1094
processed test1 633 / 1094
processed test1 634 / 1094
p

processed test1 902 / 1094
processed test1 903 / 1094
processed test1 904 / 1094
processed test1 905 / 1094
processed test1 906 / 1094
processed test1 907 / 1094
processed test1 908 / 1094
processed test1 909 / 1094
processed test1 910 / 1094
processed test1 911 / 1094
processed test1 912 / 1094
processed test1 913 / 1094
processed test1 914 / 1094
processed test1 915 / 1094
processed test1 916 / 1094
processed test1 917 / 1094
processed test1 918 / 1094
processed test1 919 / 1094
processed test1 920 / 1094
processed test1 921 / 1094
processed test1 922 / 1094
processed test1 923 / 1094
processed test1 924 / 1094
processed test1 925 / 1094
processed test1 926 / 1094
processed test1 927 / 1094
processed test1 928 / 1094
processed test1 929 / 1094
processed test1 930 / 1094
processed test1 931 / 1094
processed test1 932 / 1094
processed test1 933 / 1094
processed test1 934 / 1094
processed test1 935 / 1094
processed test1 936 / 1094
processed test1 937 / 1094
processed test1 938 / 1094
p

In [23]:
import os
import time
import sys
import torch
from PIL import Image
from torch.autograd import Variable
from torchvision import transforms
from pathlib import Path
# from nets import DGNLNet_fast
# from misc import check_mkdir
import matplotlib.pyplot as plt

ckpt = "/home/gregory/Documents/RainPerception/RainRemoval/Copied/ckpt/DGNLNet/40000_test.pth"

os.environ['CUDA_VISIBLE_DEVICES'] = '0'

torch.manual_seed(2019)
torch.cuda.set_device(0)

transform = transforms.Compose([
    transforms.Resize([512,1024]),
    transforms.ToTensor() ])

to_pil = transforms.ToPILImage()



if __name__ == '__main__':
    root = "/home/gregory/Documents/RainPerception/RainRemoval/Copied"
    input = open(os.path.join(root, 'data/test_images.txt'))
    i = 0
    image = [(os.path.join(root, 'data/images', img_name.strip('\n'))) for img_name in
                 input]
    input.close()

    # image = image[1000:]

    for img in image:
    # img = "/content/drive/MyDrive/test images/test_carla_H.png"

      net = DGNLNet().cuda()
      net = nn.DataParallel(net)
      net.to(torch.device("cuda"))

      net.load_state_dict(torch.load(ckpt,map_location=lambda storage,loc: storage.cuda(0)))

      net.eval()
      
      name = img.split("/")[-1]
      img = Image.open(Path(img))
      if len(img.getbands()) == 4:
        temp = np.asarray(img)
        temp = temp[:,:,:3]
        img = Image.fromarray(temp)
      # if isinstance(img,Image.Image):
      #     img = img.convert("RGB")
      # else:
      #     img = Image.open(Path(img))
      #     img = img.convert("RGB")
      # # plt.figure(figsize=(12,6))
      # plt.axis("off")
      # plt.imshow(img)
      with torch.no_grad():

          w, h = img.size
          img_var = Variable(transform(img).unsqueeze(0)).cuda()
          
          res = net(img_var)

          torch.cuda.synchronize()

          result = transforms.Resize((h, w))(to_pil(res.data.squeeze(0).cpu()))
          # fig = plt.figure(figsize=(16, 8))
          # fig.add_subplot(2,1,1)
          # plt.figure(figsize=(12,6))
          # plt.axis("off")
          # plt.imshow(img)
          # # fig.add_subplot(2,1,2)
          # plt.figure(figsize=(12,6))
          # plt.axis("off")
          # plt.imshow(result)
          i += 1
          print(i)
          result.save("/home/gregory/Documents/RainPerception/RainRemoval/Copied/generated_test/"+ name) 

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


1861
1862
1863
1864
1865
1866
1867
1868
1869
1870
1871
1872
1873
1874
1875
1876
1877
1878
1879
1880
1881
1882
1883
1884
1885
1886
1887
1888
1889
1890
1891
1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060


In [26]:
import os
import time
import sys
import torch
from PIL import Image
from torch.autograd import Variable
from torchvision import transforms
from pathlib import Path
# from nets import DGNLNet_fast
# from misc import check_mkdir
import matplotlib.pyplot as plt

ckpt = "/home/gregory/Documents/RainPerception/RainRemoval/Copied/ckpt/DGNLNet/22_test.pth"

#os.environ['CUDA_VISIBLE_DEVICES'] = '0'

#torch.manual_seed(2019)
#torch.cuda.set_device(0)

transform = transforms.Compose([
    transforms.Resize([512,1024]),
    transforms.ToTensor() ])

to_pil = transforms.ToPILImage()



if __name__ == '__main__':
    root = "/home/gregory/Documents/RainPerception/RainRemoval/Copied"
    
    
    img = "/home/gregory/Documents/RainPerception/RainRemoval/Copied/generated_test/1647760644.0353005_rain_M.png"

    # net = DGNLNet().cuda()

    # net.load_state_dict(torch.load(ckpt,map_location=lambda storage,loc: storage.cuda(0)))

    # net.eval()
    
    # name = img.split("/")[-1]
    img = Image.open(Path(img))
    if len(img.getbands()) == 4:
      temp = np.asarray(img)
      temp = temp[:,:,:3]
      img = Image.fromarray(temp)
    if isinstance(img,Image.Image):
        img = img.convert("RGB")
    else:
        img = Image.open(Path(img))
        img = img.convert("RGB")
    # # # plt.figure(figsize=(12,6))
    # # plt.axis("off")
    # # plt.imshow(img)
    # with torch.no_grad():

    #     w, h = img.size
    #     img_var = Variable(transform(img).unsqueeze(0)).cuda()
        
    #     res = net(img_var)

    #     torch.cuda.synchronize()

    #     result = transforms.Resize((h, w))(to_pil(res.data.squeeze(0).cpu()))
    #     fig = plt.figure(figsize=(16, 8))
    #     fig.add_subplot(2,1,1)
    #     plt.figure(figsize=(12,6))
    #     plt.axis("off")
    #     plt.imshow(img)
    #     # fig.add_subplot(2,1,2)
    #     plt.figure(figsize=(12,6))
    #     plt.axis("off")
    #     plt.imshow(result)

In [27]:
import cv2
import math
import numpy as np

def ssim(img1,img2):

    C1 = (0.01 * 255)**2
    C2 = (0.03 * 255)**2

    img1 = img1.astype(np.float64)
    img2 = img2.astype(np.float64)
    kernel = cv2.getGaussianKernel(11, 1.5)
    window = np.outer(kernel, kernel.transpose())

    mu1 = cv2.filter2D(img1, -1, window)[5:-5, 5:-5]  # valid
    mu2 = cv2.filter2D(img2, -1, window)[5:-5, 5:-5]
    mu1_sq = mu1**2
    mu2_sq = mu2**2
    mu1_mu2 = mu1 * mu2

    sigma1_sq = cv2.filter2D(img1**2, -1, window)[5:-5, 5:-5] - mu1_sq
    sigma2_sq = cv2.filter2D(img2**2, -1, window)[5:-5, 5:-5] - mu2_sq
    sigma12 = cv2.filter2D(img1 * img2, -1, window)[5:-5, 5:-5] - mu1_mu2

    ssim_map = ((2 * mu1_mu2 + C1) * (2 * sigma12 + C2)) / ((mu1_sq + mu2_sq + C1) *
                                                            (sigma1_sq + sigma2_sq + C2))
    return ssim_map.mean()

def psnr(img1,img2):

    img1 = img1.astype(np.float64)
    img2 = img2.astype(np.float64)
    mse = np.mean((img1 - img2)**2)
    if mse == 0:
        return float('inf')
    return 20 * math.log10(255.0 / math.sqrt(mse))

In [28]:
img1 = cv2.imread("/home/gregory/Documents/RainPerception/RainRemoval/Copied/data/images/val/carla/1647760470.3255076_rain_H.png")
img2 = cv2.imread("/home/gregory/Documents/RainPerception/RainRemoval/Copied/generated_test/1647760470.3255076_rain_H.png")

psnr(img1,img2),ssim(img1,img2)

(12.583845247634082, 0.835781463510365)

In [29]:
import os
import time
import sys
import torch
from PIL import Image
from torch.autograd import Variable
from torchvision import transforms
from pathlib import Path
import matplotlib.pyplot as plt
import numpy as np
# from nets import DGNLNet

class RainRemoval:
    def __init__(self,model):
        self.model = model

    def infer(self,img,flag = True):

        os.environ['CUDA_VISIBLE_DEVICES'] = '0'

        torch.manual_seed(2019)
        torch.cuda.set_device(0)

        transform = transforms.Compose([
            transforms.Resize([512,1024]),
            transforms.ToTensor() ])

        to_pil = transforms.ToPILImage()    


        if type(img) == str:
          img = np.asarray(Image.open(img))
          
        net = DGNLNet().cuda()

        net.load_state_dict(torch.load(self.model,map_location=lambda storage,loc: storage.cuda(0)))

        net.eval()

        if img.shape[-1] == 4:
            img = img[:,:,:-1]

        self.img_infer = Image.fromarray(img)

        with torch.no_grad():

            w, h = self.img_infer.size
            img_var = Variable(transform(self.img_infer).unsqueeze(0)).cuda()
            
            res = net(img_var)

            torch.cuda.synchronize()

            self.result = transforms.Resize((h, w))(to_pil(res.data.squeeze(0).cpu()))

            self.result_np = np.array(self.result)
        
        if flag:
            return self.result_np
        else:
            return self.result
    
    def displayRes(self):

        fig = plt.figure(figsize=(14, 7))
        
        fig.add_subplot(1,2,1)
        plt.axis("off")
        plt.imshow(self.img_infer)
        
        fig.add_subplot(1,2,2)
        plt.axis("off")
        plt.imshow(self.result)